In [4]:
import numpy as np

import qiskit
from qiskit import QuantumCircuit
from qiskit import transpile
from qiskit_aer.primitives import Sampler, Estimator
# from qiskit.primitives import Estimator
from qiskit.circuit import ParameterVector
from qiskit.quantum_info import SparsePauliOp
from qiskit import  Aer
from qiskit_aer.noise import NoiseModel
from qiskit_ibm_provider import IBMProvider

from sklearn.model_selection import train_test_split
import time
from matplotlib import pyplot as plt
from sklearn.metrics import confusion_matrix
from sklearn.metrics import ConfusionMatrixDisplay

import os


import LHC_QML_module as lqm

In [2]:
n_qubits = 3
num_layers = 5

# weights_init = 0.5 * np.random.randn(num_layers, n_qubits, requires_grad=True)
weights_init = 0.5 * np.random.randn(num_layers , n_qubits)
weights_init = weights_init.flatten()

In [3]:
provider = IBMProvider()
backend = provider.get_backend('ibm_brisbane')
noise_model = NoiseModel.from_backend(backend)



In [5]:
qc_template = QuantumCircuit(n_qubits)

par_inputs = ParameterVector("input", n_qubits)
par_weights = ParameterVector("weights", num_layers * n_qubits)

for i in range(n_qubits):
    qc_template.rx(par_inputs[i], i)

for i in range(n_qubits):
    qc_template.ry(par_weights[i], i)

for i in range(n_qubits):
    qc_template.cx(i, (i+1)%n_qubits)

for i in range(n_qubits):
    qc_template.rz(par_weights[i+3], i)

for i in range(n_qubits):
    qc_template.cx(i, (i+1)%n_qubits)

for i in range(n_qubits):
    qc_template.rx(par_weights[i+6], i)

for i in range(n_qubits):
    qc_template.cx(i, (i+1)%n_qubits)

for i in range(n_qubits):
    qc_template.rz(par_weights[i+9], i)

for i in range(n_qubits):
    qc_template.cx(i, (i+1)%n_qubits)

for i in range(n_qubits):
    qc_template.rz(par_weights[i+12], i)

for i in range(n_qubits):
    qc_template.cx(i, (i+1)%n_qubits)


# qc_template.measure_all()
obs = SparsePauliOp("XXI")

In [6]:
qc_template.draw()

┌──────────────┐┌────────────────┐          ┌───┐┌────────────────┐     »
q_0: ┤ Rx(input[0]) ├┤ Ry(weights[0]) ├──■───────┤ X ├┤ Rz(weights[3]) ├──■──»
     ├──────────────┤├────────────────┤┌─┴─┐     └─┬─┘├────────────────┤┌─┴─┐»
q_1: ┤ Rx(input[1]) ├┤ Ry(weights[1]) ├┤ X ├──■────┼──┤ Rz(weights[4]) ├┤ X ├»
     ├──────────────┤├────────────────┤└───┘┌─┴─┐  │  ├────────────────┤└───┘»
q_2: ┤ Rx(input[2]) ├┤ Ry(weights[2]) ├─────┤ X ├──■──┤ Rz(weights[5]) ├─────»
     └──────────────┘└────────────────┘     └───┘     └────────────────┘     »
«          ┌───┐┌────────────────┐          ┌───┐ ┌────────────────┐          »
«q_0: ─────┤ X ├┤ Rx(weights[6]) ├──■───────┤ X ├─┤ Rz(weights[9]) ├──■───────»
«          └─┬─┘├────────────────┤┌─┴─┐     └─┬─┘┌┴────────────────┤┌─┴─┐     »
«q_1: ──■────┼──┤ Rx(weights[7]) ├┤ X ├──■────┼──┤ Rz(weights[10]) ├┤ X ├──■──»
«     ┌─┴─┐  │  ├────────────────┤└───┘┌─┴─┐  │  ├─────────────────┤└───┘┌─┴─┐»
«q_2: ┤ X ├──■──┤ Rx(weights[8]) ├─────┤ X ├──■──┤ Rz(weights[11]) ├─────┤ X ├»
«     └───┘     └────────────────┘     └───┘     └─────────────────┘     └───┘»
«     ┌───┐┌─────────────────┐          ┌───┐
«q_0: ┤ X ├┤ Rz(weights[12]) ├──■───────┤ X ├
«     └─┬─┘├─────────────────┤┌─┴─┐     └─┬─┘
«q_1: ──┼──┤ Rz(weights[13]) ├┤ X ├──■────┼──
«       │  ├─────────────────┤└───┘┌─┴─┐  │  
«q_2: ──■──┤ Rz(weights[14]) ├─────┤ X ├──■──
«          └─────────────────┘     └───┘

In [7]:
transpiled_template = transpile(qc_template, backend)

In [8]:
transpiled_template.draw()

global phase: π
                                                                         »
    ancilla_0 -> 0 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_1 -> 1 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_2 -> 2 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_3 -> 3 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_4 -> 4 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_5 -> 5 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_6 -> 6 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_7 -> 7 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_8 -> 8 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_9 -> 9 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_10 -> 10 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_11 -> 11 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_12 -> 12 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_13 -> 13 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_14 -> 14 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_15 -> 15 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_16 -> 16 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_17 -> 17 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_18 -> 18 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_19 -> 19 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_20 -> 20 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_21 -> 21 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_22 -> 22 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_23 -> 23 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_24 -> 24 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_25 -> 25 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla

In [9]:
transpiled_template = transpile(qc_template, backend, optimization_level=3)

In [10]:
transpiled_template.draw()

global phase: 3π/2
                                                                         »
    ancilla_0 -> 0 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_1 -> 1 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_2 -> 2 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_3 -> 3 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_4 -> 4 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_5 -> 5 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_6 -> 6 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_7 -> 7 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_8 -> 8 ──────────────────────────────────────────────────────»
                                                                         »
    ancilla_9 -> 9 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_10 -> 10 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_11 -> 11 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_12 -> 12 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_13 -> 13 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_14 -> 14 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_15 -> 15 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_16 -> 16 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_17 -> 17 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_18 -> 18 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_19 -> 19 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_20 -> 20 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_21 -> 21 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_22 -> 22 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_23 -> 23 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_24 -> 24 ──────────────────────────────────────────────────────»
                                                                         »
  ancilla_25 -> 25 ──────────────────────────────────────────────────────»
                                                                         »
  anci